In [1]:
import xmltodict, json
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt

In [2]:
# 与えられたnode idから対応するX,Yの点を返す関数
def findXY(node_id):
    for node in nodes:
        if node['@nid'] == str(node_id):
            return (node['@x'], node['@y'])
            
# 4点から面積を計算する方法（靴紐の公式））
def shoelace_area(points):
    """
    計算順に並んだ4点の(x, y)座標リスト [(x1, y1), (x2, y2), (x3, y3), (x4, y4)] から面積を求める
    """
    n = len(points)
    area = 0
    for i in range(n):
        j = (i + 1) % n  # 次の点（最後の点は最初の点につなげる）
        area += points[i][0] * points[j][1] - points[i][1] * points[j][0]
    return abs(area) / 2

# ✅ 例: 4点を指定して計算
points = [(1, 1), (4, 1), (4, 5), (1, 5)]  # 長方形
# print(shoelace_area(points))  # 出力: 12.0

In [3]:
data = 'liml/beam1_opti_1.liml'

In [4]:
import xmltodict
import pprint

# Open the file and read the contents
with open(data,  'r', encoding='utf-8') as file:
    my_xml = file.read()

# Use xmltodict to parse and convert 
# the XML document
my_dict = xmltodict.parse(my_xml)

# Print the dictionary
pprint.pprint(my_dict, indent=2)


{ 'liml8': { 'analysis': {'@type': 'S20'},
             'displacement': [ { '@axis': '1',
                                 '@selection': 'Unnamed',
                                 'value': '0'},
                               { '@axis': '2',
                                 '@selection': 'Unnamed(2)',
                                 'value': '0'}],
             'elset': { '@color': '-6710887',
                        '@material': 'Material',
                        '@name': 'Default',
                        'elem': [ { '@eid': '1',
                                    '@nodes': '1243 1269 3 1244',
                                    '@shape': 'quad4'},
                                  { '@eid': '2',
                                    '@nodes': '1 30 31 5',
                                    '@shape': 'quad4'},
                                  { '@eid': '3',
                                    '@nodes': '5 31 32 6',
                                    '@shape': 'quad4'},
         

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



In [11]:
liml = xmltodict.unparse(my_dict, pretty=True, full_document=False)
liml
fout = open('out.liml', 'w')
fout.write(liml)
fout.close()

In [69]:
# グローバルなパラメータ
a = 0.5
E0 = 200e9
n = 2 #3が適当??
nu = 0.3

In [70]:
# FEMの結果を変数に格納
elems = my_dict['liml8']['elset']['elem'] #elements
nodes = my_dict['liml8']['node'] #nodes
result_elems = my_dict['liml8']['solution']['results']['elem']
ne = len(elems)
sigmas = np.zeros((ne,3))
rhos = np.ones(ne) * a
Es = np.zeros(ne)
vs = np.zeros(ne)
# Load stress from each element
lambda_tmp = 0
for i in range(ne):
    Es[i] = rhos[i]**n * E0
    sigma_x = np.array(list(map(lambda x: x['@stressxx'], result_elems[i]['localnode'])),dtype=np.double).sum()
    sigma_y = np.array(list(map(lambda x: x['@stressyy'], result_elems[i]['localnode'])),dtype=np.double).sum()
    tau_xy = np.array(list(map(lambda x: x['@stressxy'], result_elems[i]['localnode'])),dtype=np.double).sum()
    sigmas[i] = np.array([sigma_x,sigma_y,tau_xy])
    lambda_tmp += np.dot(nu*sigmas[i], sigmas[i].transpose())/(rhos[i]**n)
    node_ids = elems[i]['@nodes'].split(' ')
    vertices = np.zeros((4, 2))
    for j in range(4):
        (x,y) = findXY(node_ids[j])
        vertices[j, :] = (x,y)
    vs[i] = shoelace_area(vertices)

# トータルの体積V0
V0 = vs.sum()  
# lambda_barはlmbdaの初期値
lambda_bar = -1/ne*(n-1)/E0 * lambda_tmp     
lmbda = lambda_bar
dlambda = 0.1 * lambda_bar
drho = 0.05

In [71]:
tolerance = 0.01 
g_prev = 0
lmbda_prev = 0
for i in range(ne):
    while True:
        # λにしたがってρiを計算する
        rhos[i] = calc_rho_i(lmbda, sigmas[i])
        D, rhos[i] = update_D_and_rho_i(rhos[i], lmbda, sigmas[i])
        if check_if_all_rhos_are_settled(rhos): 
            break 
        g = calc_g(rhos)
        if g==g_prev: #gに変化が見られない場合、λの最適解と判定、
            break
        if abs(g/V0) < tolerance: #gが0に近づいたらλの最適解と判定
            break
        lmbda = update_lambda(g, lmbda)
        print(g, lmbda)
        if lmbda>0:
            # lmbda must be negative
            lmbda = lmbda + dlambda # λが正になったらλを負の値にもどす (dlambda < 0 )
            break
        if lmbda*lmbda_prev < 0: #λの符号が変わったらλの最適解と判定
            break
        g_prev = g
        lmbda_prev = lmbda

-1.16555207561305 -9.39065077266585e-09
1.4723636103426543 -8.536955247878046e-09
3.359426926298511 -7.68325972309024e-09
4.944886199867142 -6.829564198302436e-09
6.307019786854653 -5.975868673514631e-09
7.488915090964383 -5.122173148726826e-09
8.513000080336042 -4.268477623939021e-09
9.394285461717118 -3.4147820991512167e-09
10.145443201495254 -2.561086574363412e-09
10.782997408246956 -1.7073910495756077e-09
11.343245173275136 -8.536955247878031e-10
11.964794151716887 1.4475660719677984e-24
11th element done
11.97551489250418 1.4475660719677984e-24
12th element done
11.510617668991472 1.4475660719677984e-24
13th element done
11.04572044547831 1.4475660719677984e-24
14th element done
11.056441186266056 1.4475660719677984e-24
15th element done
11.677990164707353 1.4475660719677984e-24
16th element done
12.955165526314431 1.4475660719677984e-24
17th element done
14.916357466021509 1.4475660719677984e-24
18th element done
17.589241507450424 1.4475660719677984e-24
19th element done
21.0067

In [58]:
def calc_g(rhos):
    tmp_sum = 0
    for i in range(ne):
        tmp_sum += rhos[i] * vs[i]
    g = tmp_sum - a*V0
    return g 

In [59]:
def calc_rho_i(lmbda, sigma_i):
    rho_i = (-(n-1)/E0 * np.dot(nu*sigma_i, sigma_i.transpose())  / lmbda ) ** (1/n)
    return rho_i 

In [60]:
def calc_D(rho_i, lmbda, sigma_i):
    D = -lmbda * E0 * rho_i**n / ((n-1) * np.dot(nu*sigma_i, sigma_i.transpose()))
    return D

In [61]:
def update_D_and_rho_i(rho_i, lmbda, sigma_i):
    D = calc_D(rho_i, lmbda, sigma_i)
    while abs(D-1) > 1e-3:
        if D > 1:
            rho_i = rho_i - drho 
        else:
            rho_i = rho_i + drho
        if rho_i > 1:
            rho_i = 1 
            break 
        elif rho_i < 0.01:
            rho_i = 0.01
            break 
        D = calc_D(rho_i,lmbda, sigma_i)
    return (D, rho_i)

In [62]:
def update_lambda(g, lmbda):
    if g<0:
        lmbda = lmbda + dlambda
    else:
        lmbda = lmbda - dlambda
    return lmbda 

In [63]:
def check_if_all_rhos_are_settled(rhos):
    for i in range(ne):
        if (rhos[i] == 1) or (rhos[i] == 0.01):
            continue
        else:
            return False
    return True

In [64]:
lmbda

-8.536955247878046e-09

In [51]:
# Write to LIML file
# FEM on LISA
# Load FEM file
# Set initial lambda

IndentationError: unexpected indent (3532217043.py, line 5)

In [83]:
my_dict['liml8']['solution']

{'analysis': {'@type': 'S20'},
 'node': [{'@nid': '1', '@x': '0', '@y': '0', '@z': '0'},
  {'@nid': '2', '@x': '70', '@y': '0', '@z': '0'},
  {'@nid': '3', '@x': '70', '@y': '40', '@z': '0'},
  {'@nid': '4', '@x': '0', '@y': '40', '@z': '0'},
  {'@nid': '5', '@x': '0', '@y': '1.53846153846154', '@z': '0'},
  {'@nid': '6', '@x': '0', '@y': '3.07692307692308', '@z': '0'},
  {'@nid': '7', '@x': '0', '@y': '4.61538461538462', '@z': '0'},
  {'@nid': '8', '@x': '0', '@y': '6.15384615384615', '@z': '0'},
  {'@nid': '9', '@x': '0', '@y': '7.69230769230769', '@z': '0'},
  {'@nid': '10', '@x': '0', '@y': '9.23076923076923', '@z': '0'},
  {'@nid': '11', '@x': '0', '@y': '10.7692307692308', '@z': '0'},
  {'@nid': '12', '@x': '0', '@y': '12.3076923076923', '@z': '0'},
  {'@nid': '13', '@x': '0', '@y': '13.8461538461538', '@z': '0'},
  {'@nid': '14', '@x': '0', '@y': '15.3846153846154', '@z': '0'},
  {'@nid': '15', '@x': '0', '@y': '16.9230769230769', '@z': '0'},
  {'@nid': '16', '@x': '0', '@y': '1